In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import datetime, os
import math as math
import matplotlib.pyplot as plt
import cv2
from tqdm import tqdm
from skimage.metrics import structural_similarity

In [2]:
from tqdm.notebook import tqdm
import logging

In [3]:
df = pd.read_csv('./input/boneage-training-dataset.csv')

In [5]:
#now we will Create and configure logger 
logging.basicConfig(filename="bone_age_image_processing.log", 
                    format='%(asctime)s %(message)s', 
                    filemode='w') 

#Let us Create an object 
logger=logging.getLogger() 

#Now we are going to Set the threshold of logger to DEBUG 
logger.setLevel(logging.DEBUG) 

In [6]:
def get_dataset():
    #loading dataframes
    train_df = pd.read_csv('./input/boneage-training-dataset.csv')
    test_df = pd.read_csv('./input/boneage-test-dataset.csv')

    #appending file extension to id column for both training and testing dataframes
    train_df['id'] = train_df['id'].apply(lambda x: str(x)+'.png')
    test_df['Case ID'] = test_df['Case ID'].apply(lambda x: str(x)+'.png') 
    train_df['gender'] = train_df['male'].apply(lambda x: 'male' if x else 'female')
    return train_df, test_df

In [7]:
train_df,_ = get_dataset()

In [8]:
def pre_processing(image, quantile):
    orginal_image = image.copy()
    gray_image  = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    gray_image = cv2.GaussianBlur(gray_image, (51, 51), 0)
    #plt.hist(gray_image.ravel(),256,[0,256]); plt.show()
    #gray_image = cv2.blur(gray_image,ksize=(5,5))
    gray_image = cv2.equalizeHist(gray_image)
    #plt.hist(gray_image.ravel(),256,[0,256]); plt.show()

    # applying the sharpening kernel to the image
    #sharpened = cv2.filter2D(gray_image, -1, kernel_sharpening)
    filtered_image = np.where(gray_image > np.quantile(gray_image, quantile), gray_image, 0)

    _,thresh = cv2.threshold(filtered_image, 0, 255, cv2.THRESH_BINARY + cv2.THRESH_OTSU)
    # detect the contours on the binary image using cv2.CHAIN_APPROX_NONE
    contours, hierarchy = cv2.findContours(image=thresh, mode=cv2.RETR_TREE, method=cv2.CHAIN_APPROX_NONE)

    # draw contours on the original image
    cv2.drawContours(image=orginal_image, contours=contours, contourIdx=-1, color=(255,0,0), thickness=5, lineType=cv2.LINE_AA)
    sorted_contours = sorted(contours, key=cv2.contourArea, reverse=True)
    stencil = np.zeros(image.shape).astype(image.dtype)
    contours = np.array(sorted_contours[0:1],)
    color = [255, 255, 255]
    cv2.fillPoly(stencil, contours, color)
    result = cv2.bitwise_and(image, stencil)
    result = cv2.cvtColor(result, cv2.COLOR_RGB2GRAY)
    #Create our shapening kernel, remember it must sum to one 
    #kernel_sharpening = np.array([[-1,-1,-1], 
    #                              [-1, 9,-1],
    #                              [-1,-1,-1]])
    # applying the sharpening kernel to the image
    #sharpened = cv2.filter2D(result, -1, kernel_sharpening)
    result = cv2.adaptiveThreshold(result, 255, cv2.ADAPTIVE_THRESH_MEAN_C, cv2.THRESH_BINARY, 21, 2) 
    #plt.imshow(result)
    #plt.show()
    return result

In [9]:
def get_pre_processed_base_image(image):
    orginal_image = image.copy()
    gray_image  = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    gray_image = cv2.GaussianBlur(gray_image, (51, 51), 0)
    _,thresh = cv2.threshold(gray_image, 0, 255, cv2.THRESH_BINARY + cv2.THRESH_OTSU)
    filtered_image = np.where(gray_image > np.quantile(gray_image, 0.6), gray_image, 0)
    contours, hierarchy = cv2.findContours(image=filtered_image, mode=cv2.RETR_TREE, method=cv2.CHAIN_APPROX_SIMPLE)
    cv2.drawContours(image=orginal_image, contours=contours, contourIdx=-1, color=(255,0,0), thickness=5, lineType=cv2.LINE_AA)
    sorted_contours = sorted(contours, key=cv2.contourArea, reverse=True)
    stencil = np.zeros(image.shape).astype(image.dtype)
    contours = np.array(sorted_contours[0:1],)
    color = [255, 255, 255]
    cv2.fillPoly(stencil, contours, color)
    result = cv2.bitwise_and(orginal_image, stencil)
    result = cv2.cvtColor(result, cv2.COLOR_RGB2GRAY)
    #Create our shapening kernel, remember it must sum to one 
    #kernel_sharpening = np.array([[-1,-1,-1], 
    #                              [-1, 9,-1],
    #                              [-1,-1,-1]])
    # applying the sharpening kernel to the image
    #sharpened = cv2.filter2D(result, -1, kernel_sharpening)
    brightness = np.mean(cv2.cvtColor(image, cv2.COLOR_BGR2GRAY))
    if brightness > 80:
        result = cv2.adaptiveThreshold(result, 255, cv2.ADAPTIVE_THRESH_MEAN_C, cv2.THRESH_BINARY, 21, 2)
    elif brightness > 35 and brightness < 80:
        result = cv2.adaptiveThreshold(result, 255, cv2.ADAPTIVE_THRESH_MEAN_C, cv2.THRESH_BINARY, 21, 3)
    else:
        result = cv2.adaptiveThreshold(result, 255, cv2.ADAPTIVE_THRESH_MEAN_C, cv2.THRESH_BINARY, 21, 4)
    return result

In [10]:
def find_similarities_then_select_best(first_gray, second_gray):
    # Compute SSIM between two images
    score, diff = structural_similarity(first_gray, second_gray, full=True)
    return score
    #print("Similarity Score: {:.3f}%".format(score * 100))

In [11]:
def start_finding_similarities(quantiles, image, base_image, image_name):
    sim_score_list = []
    pixel_diff_list = []
    my_score_list = []

    sum_of_pixels_of_base_image = (base_image-255).sum() 

    for idx, quantile in tqdm(enumerate(quantiles),desc=image_name , total=len(quantiles)):
        compare_to = pre_processing(image, quantile)
        sim_score = find_similarities_then_select_best(compare_to, base_image)
        sim_score_list.append(sim_score * 100)
        pixel_diff_list.append(int(sum_of_pixels_of_base_image) - int((compare_to-255).sum()))
        my_score_list.append((sim_score * 100) / abs(int(sum_of_pixels_of_base_image) - int((compare_to-255).sum())))
        #print(f"Sim_score : {sim_score} -- Quantile : {quantile:.2f} -- Pixel Diff : {pixel_diff_list[idx]} -- My Score : {my_score_list[idx]}")
        
    return sim_score_list, pixel_diff_list, my_score_list

In [12]:
def get_best_matched_image(sim_score_list, pixel_diff_list, my_score_list, quantiles, image, base_image, filename):
    max_my_score_index = None
    sum_of_pixels_of_base_image = (base_image-255).sum()
    top_5_sim_score_idx = np.array(sim_score_list).argsort()[-5:][::-1]
    top_5_pixel_diff_idx = np.array([abs(ele) for ele in pixel_diff_list]).argsort()[:5]
    common = list(set(top_5_pixel_diff_idx).intersection(top_5_sim_score_idx))
    if len(common) == 0:
        top_5_my_score_list_idx = np.array(my_score_list).argsort()[-5:][::-1]
        max_my_score_index = top_5_my_score_list_idx[0]
    else:
        max_my_score_index = my_score_list.index(np.array(my_score_list)[common].max())
    candidate = pre_processing(image, quantiles[max_my_score_index])
    #plt.imshow(candidate)
    #plt.show()
    logger.info(f"Image : {filename} -- Diff : {abs(int((candidate-255).sum()) - int(sum_of_pixels_of_base_image))} - Quantile : {quantiles[max_my_score_index]} -- My Score : {my_score_list[max_my_score_index]}")
    return candidate

In [13]:
def save_image(path, image, image_name):
    image_to_be_saved = cv2.normalize(image, dst=None, alpha=0, beta=255,norm_type=cv2.NORM_MINMAX, dtype=cv2.CV_8U)
    saving_status = cv2.imwrite(f'{path}/{image_name}', image_to_be_saved) 
    if saving_status:
        log(f"{image_name} has been saved.")
    else:
        log(f"{image_name} could not be saved !")

In [14]:
image = cv2.imread('./input/boneage-training-dataset/boneage-training-dataset/1377.png')

In [ ]:
base_image = get_pre_processed_base_image(image)

In [ ]:
plt.imshow(base_image)
plt.show()

In [ ]:
quantiles = np.arange(0.6, 0.9, 0.01)

In [ ]:
sim_scores, pixel_diff_scores, my_scores = start_finding_similarities(quantiles, image, base_image, "image_name   ")

In [ ]:
best_image = get_best_matched_image(sim_score_list=sim_scores, pixel_diff_list=pixel_diff_scores, 
                                   my_score_list=my_scores, quantiles=quantiles, image=image, base_image=base_image)

In [15]:
quantiles = np.arange(0.6, 0.9, 0.01)
path = "/tf/bone_age/new_dataset"

for filename, boneage in (list(train_df[['id','boneage']].values)):
    fname = './input/boneage-training-dataset/boneage-training-dataset/'+ filename
    image = cv2.imread(fname)
    
    base_image = get_pre_processed_base_image(image)
    sim_scores, pixel_diff_scores, my_scores = start_finding_similarities(quantiles, image, base_image, filename)
    best_image = get_best_matched_image(sim_score_list=sim_scores, pixel_diff_list=pixel_diff_scores, 
                                   my_score_list=my_scores, quantiles=quantiles, image=image, base_image=base_image,filename=filename)
    save_image(path, best_image, filename)

1377.png:   0%|          | 0/31 [00:00<?, ?it/s]

1378.png:   0%|          | 0/31 [00:00<?, ?it/s]

1379.png:   0%|          | 0/31 [00:00<?, ?it/s]

1380.png:   0%|          | 0/31 [00:00<?, ?it/s]

1381.png:   0%|          | 0/31 [00:00<?, ?it/s]

...

15605.png:   0%|          | 0/31 [00:00<?, ?it/s]

15606.png:   0%|          | 0/31 [00:00<?, ?it/s]

15608.png:   0%|          | 0/31 [00:00<?, ?it/s]

15609.png:   0%|          | 0/31 [00:00<?, ?it/s]

15610.png:   0%|          | 0/31 [00:00<?, ?it/s]

In [16]:
DIR = './new_dataset'
print(len([name for name in os.listdir(DIR) if os.path.isfile(os.path.join(DIR, name))]))

11494
